In [1]:
import pandas as pd
import numpy as np
import csv
import math
import re
import datetime

In [2]:
n = 0
data = []
with open('data/vacs_train.csv', newline='', encoding='utf-8') as csvfile:
    reader = csv.DictReader(csvfile, delimiter=';')
    for row in reader:
        n += 1
        data.append(row)
df = pd.DataFrame(data)

In [3]:
for c in ['company.id','salary_from']:
    df[c] = pd.to_numeric(df[c])

In [4]:
df = df.sort_values(by='publication_date', ascending=True)

In [5]:
def tokenize(text: str):
    text = text.replace(' ', '').replace('\t', '').lower()
    tokens = []
    current_token = ''

    for c in text:
        if c.isdigit() == current_token.isdigit():
            current_token += c
        else:
            if len(current_token) > 0:
                tokens.append(current_token)
            current_token = c

    if len(current_token) > 0:
        tokens.append(current_token)

    tokens += ['#', '#', '#']

    return tokens


def salary_from_str(salary: str):
    try:
        res = int(salary)
    except:
        return 0
    if res < 100:
        res *= 1000
    return res


def starts_with_any_of(text: str, indicators: [str]) -> bool:
    for ind in indicators:
        if text.startswith(ind):
            return True
    return False


def has_any_of(text: str, indicators: [str]) -> bool:
    for ind in indicators:
        if text.find(ind) != -1:
            return True
    return False


def evaluate_priority(text: str, priorities: {str:int}) -> int:
    priority = 0
    for k in priorities:
        if text.find(k) != -1:
            priority += priorities[k]
    return priority


def find_salaries(tokens):
    range_indicators = ['-', 'до', 'р.до', 'руб.до', 'рубдо', 'р.-', 'р-', 'руб.-', 'руб-']
    percent_indicators = ['+%', '+преми', '+бонус', 'плюс', 'процент', 'преми', 'бонус']
    salary_indicators = ['тыс', 'т.р', 'руб']
    hour_indicators = [':', '.', '/']
    priority_indicators = {'возмож': -3, 'лучши': -2, 'заработн': 3, 'оклад': 2, 'совокупн': 3, 'ежемесячн': 1,
                           'доход': 3, 'испытат': 1, 'после': 1, 'дополнит': -1}
    bonus_correction = 5000

    ranges = []

    i = 0
    while i + 2 < len(tokens):
        t0 = tokens[i - 1] if i > 0 else ''

        t1 = tokens[i]
        if not t1.isdigit():
            i += 1
            continue

        t2 = tokens[i + 1]
        t3 = tokens[i + 2]

        t4 = tokens[i + 3] if i + 3 < len(tokens) else ''

        salary_from = salary_from_str(t1)
        priority = evaluate_priority(t0, priority_indicators)

        if t0.find('ISO') != -1:
            i += 1
            continue

        if (t2 in hour_indicators) and not starts_with_any_of(t4, salary_indicators):
            i += 3
            continue

        if (t2 in range_indicators) and t3.isdigit() and \
                (len(t1) >= 5 and len(t3) >= 5
                or
                starts_with_any_of(t4, salary_indicators)):
            salary_to = salary_from_str(t3)
            ranges.append((priority, salary_from, salary_to))
            i += 3
            continue

        if has_any_of(t2, percent_indicators) and len(t1) >= 5:
            ranges.append((priority, salary_from + bonus_correction, salary_from + bonus_correction))
            i += 2
            continue

        if starts_with_any_of(t2, salary_indicators) or (len(t1) >= 5):
            ranges.append((priority, salary_from, salary_from))
            i += 2
            continue

        i += 1

    ranges = sorted(ranges, key=lambda range:range[0])

    return ranges


def get_salary_from(text: str):
    tokens = tokenize(text)
    salaries = find_salaries(tokens)
    if len(salaries) > 0 and len(salaries) < 4:
        salary = salaries[-1][1]
        if salary < 10000 or salary > 100000:
            return None
        else:
            return salary
    else:
        return None

In [6]:
j = 0 # нашлась подстрока
correct = 0 # эта подстрока очень близка к зарплате
incorrect = 0
dif = []
extracted_salary = []
for i, row in df.iterrows():
    desc = row['description']
    salary = get_salary_from(desc)
    if salary is not None:
        extracted_salary.append(salary)
        dif.append(salary - int(row['salary_from']))
        if abs(salary - int(row['salary_from'])) <= 5000:
            correct += 1
        else:
            print(row['name'], 'found', salary, 'real', row['salary_from'])
            print(desc)
            print('\n\n')
            incorrect += 1
            #if er > 30:
            #    break
        j+=1
    else:
        extracted_salary.append(None)
        
print('Вакансий содержат в описании подстроки, похожие на зарплату: ',j,j/n,n)
#print('Вакансий, реально содержащих зарплату в описании: ',q,q/n,q/j)
print(f'Угадано зарплат: {correct}/{correct+incorrect} ({correct/(correct + incorrect)})')

Продавец-консультант (Кудрово) found 35000 real 25000.0
Наша компания занимается дистрибуцией мобильной связи компании МТС в Санкт-Петербурге. За это время мы зарекомендовали себя как надежный партнер, качественный представитель оператора связи, и добросовестный работодатель.Наши консультанты работают на фирменных точках продаж МТС в ТК и гипермаркетах.Мы сторонники активных продаж, качественного консультирования и креативного подхода к делу.Ищем активных, целеустремленных, жизнерадостных!   Обязанности:  активные продажи продукции МТС консультирование клиентов по продукции МТС ведение отчетности работа с документацией  Требования:  огромное желание зарабатывать стремление развиваться в сфере продаж пунктуальность, ответственность  Условия:  работа на точках продаж в ТЦ и гипермаркетах ежедневная выплата заработной платы! график работы с 12.00 до 22.00 5/2 или 2/2 заработная плата - оклад+%, от 35000 в графике 5/2, от 25000 в графике 2/2 никаких задержек после окончания рабочего дня бе

Инженер технического надзора (общестроительные работы) found 80000 real 60000.0
Обязанности: -Строительный контроль за выполнение строительно-монтажных работ и приемку законченных объектов от подрядных организаций; -Контроль выполнения планов капитального строительства, соответствие объемов, сроков и качества строительно-монтажных работ, а также качества применяемых материалов, изделий, конструкций утвержденной проектно-сметной документации, рабочим чертежам, строительным нормам и правилам, стандартам, техническим условиям, правилам по охране труда; -Участие в решении вопросов о внесении в проекты изменений в связи с внедрением более прогрессивных технологических процессов, объемно-планировочных и конструктивных решений, обеспечивающих снижение стоимости и улучшение технико-экономических показателей объектов строительства и рекомендации; -Участие в рассмотрении и согласовании возникающих в ходе строительства изменений проектных решений, решает вопросы по замене при необходимости матери

Менеджер по логистике found 20000 real 30000.0
Транспортно-экспедиторской компании требуется специалист - менеджер по продажам логистических услуг.   Обязанности:  Активное привлечение клиентов по автотранспортным перевозкам под собственный и привлеченный транспорт; Организация грузоперевозок и экспедиторского обслуживания клиентов; Расширение базы автоперевозчиков; Ведение внутренней документации компании; Согласование и заключение договоров/заявок с клиентами и автоперевозчиками; Подготовка презентаций и коммерческих предложений;    Требования:  Успешный опыт работы и продаж транспортно-экспедиторских услуг; Опытный пользователь ПК; Коммуникабельность, целеустремленность, нацеленность на результат, внимание к деталям, грамотная речь и умение ведения переговоров;    Условия:  Полный рабочий день с 9:00 до 18:00 (1 час перерыв на обед) Офис - 2 км от м.Звездная (Общественный транспорт от метро - автобус, маршрутное такси) Испытательный срок - 2 месяца. Заработная плата на испытательный

Javascript-разработчик found 80000 real 60000.0
Должностные обязанности: Мы предлагаем участие в работе над крупной системой корпоративного уровня, включающей в себя административный функционал, медицинский, контакт-центр, лабораторный и другое, а также некоторое количество приложений для внешних пользователей. Дополнительно в обязанности будет входить поддержание корпоративного сайта и небольшие доработки по нему.   Требования:  Отличное знание HTML, CSS, JavaScript, jQuery, node.js Умение работать с JSON и AJAX, SOAP и REST API Навыки блочной, адаптивной верстки  Будет преимуществом:  Навыки работы с js-шаблонизаторами (например Mustache) Знакомство с библиотекой Backbone или подобными Опыт работы с фреймворком AngularJS или подобными Понимание работы CSS-препроцессоров (например LESS) Умение работать с системами контроля версий (например GIT)    Условия:  Работа в крупном медицинском холдинге График работы - пятидневка Испытательный срок - 1 месяц, заработная плата на испытательном 

Менеджер по продажам found 20000 real 30000.0
О нас: Наша организация в настоящий момент активно занимается импортозамещением, производством собственной продукции, средств индивидуальной защиты (СИЗ) производственного персонала, поэтому мы будем рады появлению в нашей команде людей, готовых к обучению, познанию чего-то нового, развитию вместе с компанией.   Обязанности:  Работа с заявками с сайта и входящими звонками, холодные звонки отсутствуют; Поиск клиентов, работа с существующими Клиентами; Ведение деловых переговоров; Полное сопровождение заказов (заключение договоров, выставление спецификаций и счетов, отслеживание выполнение заказа, отгрузки готовой продукции); Формирование коммерческих предложений; Подготовка отчетов по заданной форме; Работа с клиентской базой.  Требования:  Технически грамотным отдается предпочтение; Грамотная устная и письменная речь; Уверенный пользователь MS Office (Word, Excel); Знание 1С- будет вашим преимуществом; Готовы рассмотреть кандидатов без опыт

...

Продавец-консультант found 10000 real 40000.0
Сейлеры Внимание: мы указываем только реальную заработную плату! Высокая заработная плата гарантирована, также имеется интересная и мотивирующая система бонусов!   Компания ООО "Т28" была основана в 2004 году.Мы осуществляем прямые поставки верхней одежды и обуви по средствам морского порта в г . Санкт-Петербург на прямую от производителей, минуя перекупщиков и все возможных посредников. Компания работает по принципу ПРОИЗВОДИТЕЛЬ-ПОКУПАТЕЛЬ. Обязанности:  3 дня подготовки к распродажам /3 дня реализации (продажи) Три дня в неделю команды занимается организационной работой ( занимаются поиском аренды для распродаж, подготовка торговой площадки к распродажам) Базы арендодателей предоставляются. Своя типография и своя логистика.( неполный рабочий день ) После организации , ребята проводят Дисконт-распродажи (3 дня в неделю, в разных районах города) Управление операционной деятельностью торговых площадок ( открытие/закрытие) Мерчендайзинг на т

Менеджер по продажам в отделение банка (Лиговский проспект) found 100000 real 40000.0
ПАО "Совкомбанк" Вакансия: Финансовый консультант. Крупнейший и прибыльный федеральный банк открыл вакансию для амбициозных и уверенных в себе в связи с динамичным развитием и открытием новых офисов.   Обязанности: - активный поиск новых клиентов: звонки, проведение промо-акций и др. - консультирование входящих клиентов по продуктам и услугам банка: кредиты, вклады, страхование, НПФ, переводы и др. - выполнение плана продаж и установленных нормативов   Требования: - желателен опыт работы в активных продажах или опыт работы в банковском секторе - желание общаться с людьми, продавать и хорошо зарабатывать – обязательное требование! - желание следовать ценностям Банка - готовность учиться продажам и разнообразным финансовым инструментам.   Условия: - оформление по ТК РФ - официальная заработная плата и ежемесячная неограниченная премия, лучшие зарабатывают от 100000 рублей - расширенный соц пакет для вас

Мастер-консультант found 100000 real 60000.0
ДЦ «CTK Center» (официальный дилер Nissan) приглашает на работу мастера-консультанта отдела сервиса автомобилей. Требования:  высшее техническое образование хорошее знание технического устройства автомобиля, базовые знания технологий продаж опытный пользователь ПК для нас важны такие качества как: ответственность, честность, вежливость, доброжелательность, коммуникабельность, грамотно поставленная речь, активная жизненная позиция.  Обязанности:  консультация клиентов по телефону и при личной встрече, запись на ремонт продажа дополнительных услуг и сервисных продуктов прием автомобилей клиентов на сервис, оформление необходимой документации ведение автомобиля клиента от приема до выдачи, согласование видов и стоимости работ, запасных частей выполнение стандартов по обслуживанию клиентов СТК Центр и компании Ниссан  Мы предлагаем:  работу в стабильной компании со сложившимися процедурами сменный график работы (2/2/3 с 8:30 до 21:00) заработная

Менеджер по продажам (мебель) found 100000 real 45000.0
Должностные обязанности: Мы являемся самым крупным дилером в Санкт-Петербурге- 22 салона элитной мебели, индивидуальные дизайн-проекты! Бренд кухни "Мария" - марка года №1!!  Что Вас ждет в наших салонах:  Консультирование клиентов в интерьерном салоне Составление индивидуального дизайн-проекта кухни Расчет стоимости проекта Заключение договора с клиентом Сопровождение клиента на всех этапах сделки    Что мы ждем от кандидата?  Хорошо поставленная речь, навыки ведения переговоров Желание и стремление продавать - Продажи это 80% рабочего процесса Знание программ желательно, но не обязательно (если вы уверенный пользователь ПК, мы всему вас научим!) В приоритете опыт: в продажах, консультировании, оказании услуг.    Что Мы предлагаем:  Мы готовы Вас переквалифицировать! Проводим обучение в собственном центре переподготовки с профессиональными бизнес-тренерами! Оформляем по Трудовой книжке с Вашего первого рабочего дня! Удобный сменн

Вакансий содержат в описании подстроки, похожие на зарплату:  23968 0.23967760322396775 100001
Угадано зарплат: 19141/23968 (0.7986064753004005)


In [ ]:
#Вакансий содержат в описании подстроки, похожие на зарплату:  23968 0.23967760322396775 100001
#Угадано зарплат: 19141/23968 (0.7986064753004005)